![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Modelowanie Języka</h1>
<h2> 12. <i>Model neuronowy rekurencyjny</i>  [ćwiczenia]</h2> 
<h3> Jakub Pokrywka (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

# Ensemble modeli

W jaki sposób można podnieść wynik predykcji dla zadania uczenia maszynowego?

In [32]:
!mkdir dev-0-ireland-news

mkdir: cannot create directory ‘dev-0-ireland-news’: File exists


Mamy wyzwanie:

https://gonito.net/challenge-all-submissions/ireland-news-headlines-word-gap

https://github.com/kubapok/ireland-news-word-gap/tree/0c6557c8a3cd6d8c77f64618850b2ae82c19476a

In [33]:
!wget https://github.com/kubapok/ireland-news-word-gap/raw/11c72875023c5c01c9d0c0ca39d72c90c840aeb3/dev-0/out.tsv
!mv out.tsv ./dev-0/out-solution1.tsv
!wget https://github.com/kubapok/ireland-news-word-gap/raw/0c6557c8a3cd6d8c77f64618850b2ae82c19476a/dev-0/out.tsv
!mv out.tsv ./dev-0/out-solution2.tsv
! ( cd dev-0 ; wget https://git.wmi.amu.edu.pl/kubapok/ireland-news-word-gap-prediction/raw/branch/master/dev-0/expected.tsv)

--2022-05-13 13:23:05--  https://github.com/kubapok/ireland-news-word-gap/raw/11c72875023c5c01c9d0c0ca39d72c90c840aeb3/dev-0/out.tsv
Resolving github.com (github.com)... 140.82.121.4
Connecting to github.com (github.com)|140.82.121.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/kubapok/ireland-news-word-gap/11c72875023c5c01c9d0c0ca39d72c90c840aeb3/dev-0/out.tsv [following]
--2022-05-13 13:23:06--  https://raw.githubusercontent.com/kubapok/ireland-news-word-gap/11c72875023c5c01c9d0c0ca39d72c90c840aeb3/dev-0/out.tsv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.110.133, 185.199.111.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 63249692 (60M) [text/plain]
Saving to: ‘out.tsv’

out.tsv             100%[===================>]  60,32M  26,7MB/s    in 2,3s    

2

In [34]:
!wget https://gonito.net/get/bin/geval
!chmod u+x geval

--2022-05-13 13:23:12--  https://gonito.net/get/bin/geval
Resolving gonito.net (gonito.net)... 150.254.78.126
Connecting to gonito.net (gonito.net)|150.254.78.126|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 12860136 (12M) [application/octet-stream]
Saving to: ‘geval.1’

geval.1             100%[===================>]  12,26M  2,67MB/s    in 4,1s    

2022-05-13 13:23:16 (2,97 MB/s) - ‘geval.1’ saved [12860136/12860136]



In [35]:
!./geval --metric PerplexityHashed -o ./dev-0/out-solution1.tsv -e dev-0/expected.tsv

35.05218788086649


In [36]:
!./geval --metric PerplexityHashed -o ./dev-0/out-solution2.tsv -e dev-0/expected.tsv

33.47429048442195


In [37]:
with open('./dev-0/out-solution1.tsv') as s1, open('./dev-0/out-solution2.tsv') as s2, open('./dev-0/out-merge.tsv','w') as f_merge:
    for l1, l2 in zip(s1, s2):
        dir1 = {''.join(x.split(':')[:-1]): float(x.split(':')[-1]) for x in l1.rstrip().split(' ')}
        dir2 = {''.join(x.split(':')[:-1]): float(x.split(':')[-1]) for x in l2.rstrip().split(' ')}
        newdir = dict()
        for k in dir1.keys() | dir2.keys():
            newdir[k] = dir1[k] if k in dir1 else 0.0
            newdir[k] += dir2[k] if k in dir2 else 0.0
            newdir[k] /= 2
        merge_line = ' '.join([k + ':' + str(v) for k,v in newdir.items()]) + '\n'
        f_merge.write(merge_line)

In [38]:
!./geval --metric PerplexityHashed -o ./dev-0/out-merge.tsv -e dev-0/expected.tsv

29.054162509715063


Złożenie:

- kilku dobrych niezależnych modeli 
- kilku modeli wytrenowanych dla różnego seeda
- kilku ostatnich checkpointów

W jaki sposób składać różne modele:

- średnia ważona
- średnia geometryczna
- inna średnia
- trenowanie osobnego prostego modelu, którego zadanie to składanie modeli (np. regresja liniowa)


Można też trenować wspólnie kilka modeli jednocześnie ze wspólnym backpropagation.

Jakie są minusy ensemble?

- wyższy stopień skomplikowania modelu
- dłuższy czas inferencji
- zużycie większych zasobów komputera
- gorsza interpretowalność

W praktyce jeżeli startujemy w konkursie uczenia maszynowego, zawsze warto robić ensemble.


W komercji jeżeli mamy ograniczenia czasowe lub zasobów, model jest ciężki, wynik modelu nie jest bardzo ważny, to często nie korzysta się z ensembli.
W nauce albo kiedy chcemy porównać kilka różnych metod, to składanie modeli zaburza nam niepotrzebnie obraz.

Warto mieć na uwadze, że niektóre metody z założenia są ensemblami. Np. las losowy albo boostowane drzewa decyzyjne.

### ZADANIE

przykładowy tekst: "ala" "ma" "kota" "MASK" "2" "psy" "i" "chomika"

Stworzyć 2 sieci rekurencyjne LSTM dla Challenging America word-gap prediction. 
- jedna sieć powinna działać do przodu (czyli jak zwyczajna sieć): "ala" "ma" "kota"
- druga siec powinna działać do tyłu: "chomika" "i" "psy" "2"
    
Zrobienie sieci odwrotnej jest bardzo proste. Wystarczy odwrócić kolejność słów, nie ma potrzeby ingerować w architekturę modeli.

Następnie należy zrobić jakiś ensemble tych modeli. W najprostszej wersji może to być średnia arytmetyczna. Warto jednak spróbować innych sposobów, np. można trenować te sieci łącznie.


Wymogi takie jak zawsze, zadanie widoczne na gonito.